In [13]:
    from hicmatrix import HiCMatrix as hm
    from hicmatrix.lib import MatrixFileHandler
    import h5py
    import logging
    import numpy as np
    import pandas as pd
    from hicmatrix import HiCMatrix as hm
    from hicmatrix.lib import MatrixFileHandler
    from scipy.sparse import csr_matrix, dia_matrix, triu, tril, coo_matrix
    import scipy.stats as stats

    SRP_name="aggregates"
    resolution="10kbp_raw"
    resol_human="10000"
    prediction_type="prediction"
    
    exp_file_path=f'/grid/gillis/data/lohia/hi_c_data_processing/data_human/{SRP_name}/{resolution}/max/hic_gene_inter_KR.h5'

    jac_sim = hm.hiCMatrix(exp_file_path)
    

    all_gene_list = [x[3].decode() for x in jac_sim.cut_intervals]
    entire_matrix_KR = jac_sim.matrix


    all_non_gene_index_list = [x[1] for x in jac_sim.cut_intervals if x[3].decode() == 'non-gene']
    all_bins = [x[1] for x in jac_sim.cut_intervals]
    
    
    df_unique_variants  = pd.read_csv(f'/grid/gillis/data/lohia/eQTL/GTEx_Analysis_v8_eQTL_all_associations/all_association_all_genes.csv.gz', sep='\t')
    df_unique_variants['prediction'] = 0
    df_unique_variants['gene_chr'] = [x.split('_')[0] for x in df_unique_variants['variant_id']]
    
    #df_unique_variants = pd.read_csv('/grid/gillis/data/lohia/eQTL/GTEx_Analysis_v8_eQTL_all_associations/all_association_all.csv.gz', sep='\t' )
    #df_unique_variants['prediction'] = 0
    
    
    
    #df_unique_variants_sig   = pd.read_csv(f'/grid/gillis/data/lohia/eQTL/GTEx_Analysis_v8_eQTL/sig_association.csv.gz', sep='\t' )

    #df_unique_variants_sig = df_unique_variants_sig[df_unique_variants_sig['prediction'] >= int(tissue_threshold)]

    #df_unique_variants_sig['prediction'] = 1
    
    df_unique_variants_sig = pd.read_csv('/grid/gillis/data/lohia/eQTL/gtex_trans/GTEx_Analysis_v8_trans_eGenes_fdr05.txt', sep='\t' )
    df_unique_variants_sig['prediction'] = 1

    
    
    
    df_all_variants = pd.concat([df_unique_variants, df_unique_variants_sig])
    df_all_variants['gene_id'] = [x.split('.')[0] for x in df_all_variants['gene_id']]
    df_all_variants['chr_var'] = [x.split('_')[0] for x in df_all_variants['variant_id']]
    df_all_variants['tss_var'] = [x.split('_')[1] for x in df_all_variants['variant_id']]
    
    
    #df_all_variants = df_all_variants[df_all_variants['chr_var'] == chrom]
    df_all_variants = df_all_variants[df_all_variants['gene_id'].isin(all_gene_list)]
    
    df_all_variants['bin'] = [int(int(x)/int(resol_human)) for x in df_all_variants['tss_var']]
    df_all_variants['bin'] = df_all_variants['bin'].astype('int')
    
    df_all_variants = df_all_variants[df_all_variants['bin'].isin(all_non_gene_index_list)]
    df_all_variants['gene_bin'] = [all_gene_list.index(gene_x) for gene_x in df_all_variants['gene_id']]
    
    df_all_variants.drop_duplicates(['variant_id', 'gene_id'], keep='last', inplace=True)
    
   
    
    
    
    df_all_variants_subset = df_unique_variants_sig.drop_duplicates(['variant_id'])
    
    df_all_variants_subset['gene_id'] = [x.split('.')[0] for x in df_all_variants_subset['gene_id']]
    df_all_variants_subset['chr_var'] = [x.split('_')[0] for x in df_all_variants_subset['variant_id']]
    df_all_variants_subset['tss_var'] = [x.split('_')[1] for x in df_all_variants_subset['variant_id']]
    df_all_variants_subset = df_all_variants_subset[df_all_variants_subset['gene_id'].isin(all_gene_list)]
    
    #df_all_variants_subset = df_all_variants_subset[df_all_variants_subset['chr_var'] == chrom]
    
    
    df_all_variants_subset['bin'] = [int(int(x)/int(resol_human)) for x in df_all_variants_subset['tss_var']]
    df_all_variants_subset['bin'] = df_all_variants_subset['bin'].astype('int')
    
    df_all_variants_subset = df_all_variants_subset[df_all_variants_subset['bin'].isin(all_non_gene_index_list)]
    

    
    auc_KR = []
    auc_tss = []
    auc_gene_id = []
    auc_KR_ranked = []
    auc_KR_ranked_tss = []
    auc_jac_tss = []
    auc_jac = []
    auc_insulation_score = []
    auc_activity_score = []
    auc_var_insulation = []
    auc_var_insulation_median = []

    for var_int, gene_chr in zip(df_all_variants_subset['variant_id'].to_list(), df_all_variants_subset['gene_chr'].to_list()):
        #print (var_int)


        df_test = df_all_variants[df_all_variants['gene_chr'] != gene_chr]
        #df_test_negative = df_test[df_test['variant_id'] != var_int]
        #df_test_negative['prediction'] = 0
        #df_test_positive = df_test[df_test['variant_id'] == var_int]
        #df_test_positive['prediction'] = 1
        #df_test = pd.concat([df_test_negative, df_test_positive])
 
        #df_test = df_test[df_test['tss_distance'].abs() <= (int(distance_cutoff_in_bp)+200000+int(resol_human))]
        
        #df_test['nes'] = df_test['slope'].abs()
        #df_test['pval_st'] = 1/df_test['pval_nominal']
        df_test.drop_duplicates(['gene_bin'], keep='last', inplace=True)
        
        if df_test['prediction'].sum() != 0:
            if df_test.shape[0] > 1:
                bin_start = int(int(var_int.split('_')[1]) / int(resol_human))

                if bin_start in all_non_gene_index_list:

                            gene_bins = []
                            gene_name = []
                            non_gene_bins = []
                            variant_bins = [all_bins.index(bin_start)]


                            variant_name = [var_int]

                            for gene_x in df_test.drop_duplicates(subset = ['gene_id', 'variant_id'])['gene_id']:
                                    if gene_x in all_gene_list:
                                            gene_bins.append(all_gene_list.index(gene_x))
                                            gene_name.append(gene_x)

                                    else:
                                        continue


                            biny=gene_bins
                            binx=variant_bins
                            biny_name = gene_name
                            binx_name = variant_name




                            df_exp = pd.pivot_table(df_test, values=prediction_type, columns='gene_id',
                                                index='variant_id')


                            subset_genes_exp_file = list (set(df_exp.columns.to_list()) & set(biny_name))
                            df_exp_subset = df_exp.loc[:, subset_genes_exp_file]


                            if prediction_type == 'prediction':

                                exp_upper = lambda x: np.where(x <= 0 , 0, 1.0) if x[~np.isnan(x)].shape[0] > 0 else np.zeros(x.shape[0])
                                tp = np.apply_along_axis(exp_upper, 1, df_exp_subset)

                                exp_upper = lambda x: np.where(x > 0   , 0, 1.0) if x[~np.isnan(x)].shape[0] > 0 else np.zeros(x.shape[0])
                                tn = np.apply_along_axis(exp_upper, 1, df_exp_subset)
                            else:
                                exp_upper = lambda x: np.where(x < np.percentile(x[~np.isnan(x)] , 99), 0, 1.0) if x[~np.isnan(x)].shape[0] > 0 else np.zeros(x.shape[0])
                                tp = np.apply_along_axis(exp_upper, 1, df_exp_subset)
                                exp_upper = lambda x: np.where(x >= np.percentile(x[~np.isnan(x)] , 99), 0, 1.0) if x[~np.isnan(x)].shape[0] > 0 else np.zeros(x.shape[0])
                                tn = np.apply_along_axis(exp_upper, 1, df_exp_subset)



                            df_jac = pd.DataFrame(entire_matrix_KR[binx,:][:, biny].toarray() ,  index=binx_name, columns = biny_name)

                            df_jac_subset = df_jac.loc[:, subset_genes_exp_file]

                            rank_abs = lambda x: stats.rankdata(x)
                            predicts2 = np.apply_along_axis(rank_abs, 1, df_jac_subset)
                            predicts2 = predicts2.astype('float')

                            pos_rank_sum = tp * predicts2
                            auc_array = (((np.nansum(pos_rank_sum, axis=1) / (np.nansum(tp, axis=1)) )- (np.nansum(tp, axis=1) + 1)/2)) / np.nansum(tn, axis=1)
                            auc_KR.append(auc_array[0])

                            auc_insulation_score.append(auc_array[0])
                            auc_gene_id.append(var_int)
                            bin_start = int(int(var_int.split('_')[1]) / int(resol_human))
                            auc_var_insulation.append(df_all_variants_subset.shape[0])
                            #auc_var_insulation.append(insulation_scores_dict_orignal[bin_start])
                            auc_KR_ranked_tss.append(df_test.shape[0])
                            auc_jac_tss.append(df_test['prediction'].sum())
                            #auc_var_insulation_median.append(insulation_scores_dict[bin_start])
                            auc_var_insulation_median.append(df_all_variants_subset.shape[0])
                            auc_activity_score.append(df_all_variants_subset.shape[0])
                else:
                    continue
            else:
                continue
        else:
            continue
        df = pd.DataFrame(columns = ['auc_KR', 'gene', 'auc_insulation', 'auc_activity', 'auc_var_insulation', 'auc_var_insulation_median'])  
        df['auc_KR'] = auc_KR
        df['gene'] = auc_gene_id
        df['auc_insulation'] = auc_insulation_score
        df['auc_activity'] = auc_activity_score
        df['auc_var_insulation'] = auc_var_insulation
        df['auc_var_insulation_median'] = auc_var_insulation_median
        print (df['auc_KR'].median())
    df.to_csv(f'/grid/gillis/data/lohia/hi_c_data_processing/data_human/{SRP_name}/{resolution}/temp.csv', sep='\t', index=False)
    
    



In [58]:
df = pd.read_csv('/grid/gillis/data/lohia/hi_c_data_processing/genomes_jlee/gene2ensembl.gz', sep='\t')

In [60]:
df = df[df['#tax_id'] ==9606]

In [61]:
df

#tax_id     GeneID Ensembl_gene_identifier  \
1369408     9606          1         ENSG00000121410   
1369409     9606          2         ENSG00000175899   
1369410     9606          3         ENSG00000256069   
1369411     9606          9         ENSG00000171428   
1369412     9606          9         ENSG00000171428   
...          ...        ...                     ...   
1433784     9606  120356739         ENSG00000184154   
1433785     9606  120356739         ENSG00000184154   
1433786     9606  120356739         ENSG00000184154   
1433787     9606  120356739         ENSG00000184154   
1433788     9606  120356740         ENSG00000284844   

        RNA_nucleotide_accession.version Ensembl_rna_identifier  \
1369408                      NM_130786.4      ENST00000263100.8   
1369409                      NM_000014.6     ENST00000318602.12   
1369410                      NR_040112.1      ENST00000543404.5   
1369411                      NM_000662.8      ENST00000307719.9   
1369412                   NM_001160171.4      ENST00000518029.5   
...                                  ...                    ...   
1433784                   NM_001205138.4      ENST00000423494.6   
1433785                   NM_001271471.3     ENST00000324866.11   
1433786                   NM_001318803.2      ENST00000538478.5   
1433787                      NM_145309.6      ENST00000289488.7   
1433788                   NM_001393500.1      ENST00000541899.2   

        protein_accession.version Ensembl_protein_identifier  
1369408               NP_570602.2          ENSP00000263100.2  
1369409               NP_000005.3          ENSP00000323929.8  
1369410                         -                          -  
1369411               NP_000653.3          ENSP00000307218.4  
1369412            NP_001153643.1          ENSP00000428270.1  
...                           ...                        ...  
1433784            NP_001192067.1          ENSP00000441249.1  
1433785            NP_001258400.1          ENSP00000440693.1  
1433786            NP_001305732.1          ENSP00000444583.1  
1433787               NP_660352.1          ENSP00000289488.2  
1433788            NP_001380429.1          ENSP00000494667.1  

[64381 rows x 7 columns]

In [64]:
df_gene_name = pd.read_csv('/grid/gillis/data/lohia/hi_c_data_processing/genomes_jlee/Homo_sapiens.gene_info.gz', sep='\t')

In [66]:
df_gene_name

#tax_id   GeneID    Symbol LocusTag                   Synonyms  \
0         9606        1      A1BG        -       A1B|ABG|GAB|HYST2477   
1         9606        2       A2M        -  A2MD|CPAMD5|FWP007|S863-7   
2         9606        3     A2MP1        -                       A2MP   
3         9606        9      NAT1        -       AAC1|MNAT|NAT-1|NATI   
4         9606       10      NAT2        -            AAC2|NAT-2|PNAT   
...        ...      ...       ...      ...                        ...   
64496   741158  8923215      trnD        -                          -   
64497   741158  8923216      trnP        -                          -   
64498   741158  8923217      trnA        -                          -   
64499   741158  8923218      COX1        -                          -   
64500   741158  8923219  16S rRNA        -                          -   

                                                 dbXrefs chromosome  \
0         MIM:138670|HGNC:HGNC:5|Ensembl:ENSG00000121410         19   
1         MIM:103950|HGNC:HGNC:7|Ensembl:ENSG00000175899         12   
2                    HGNC:HGNC:8|Ensembl:ENSG00000256069         12   
3      MIM:108345|HGNC:HGNC:7645|Ensembl:ENSG00000171428          8   
4      MIM:612182|HGNC:HGNC:7646|Ensembl:ENSG00000156006          8   
...                                                  ...        ...   
64496                                                  -         MT   
64497                                                  -         MT   
64498                                                  -         MT   
64499                                                  -         MT   
64500                                                  -         MT   

      map_location                         description    type_of_gene  \
0         19q13.43              alpha-1-B glycoprotein  protein-coding   
1         12p13.31               alpha-2-macroglobulin  protein-coding   
2         12p13.31  alpha-2-macroglobulin pseudogene 1          pseudo   
3             8p22               N-acetyltransferase 1  protein-coding   
4             8p22               N-acetyltransferase 2  protein-coding   
...            ...                                 ...             ...   
64496            -                                tRNA            tRNA   
64497            -                                tRNA            tRNA   
64498            -                                tRNA            tRNA   
64499            -      cytochrome c oxidase subunit I  protein-coding   
64500            -                              l-rRNA            rRNA   

      Symbol_from_nomenclature_authority  \
0                                   A1BG   
1                                    A2M   
2                                  A2MP1   
3                                   NAT1   
4                                   NAT2   
...                                  ...   
64496                                  -   
64497                                  -   
64498                                  -   
64499                                  -   
64500                                  -   

      Full_name_from_nomenclature_authority Nomenclature_status  \
0                    alpha-1-B glycoprotein                   O   
1                     alpha-2-macroglobulin                   O   
2        alpha-2-macroglobulin pseudogene 1                   O   
3                     N-acetyltransferase 1                   O   
4                     N-acetyltransferase 2                   O   
...                                     ...                 ...   
64496                                     -                   -   
64497                                     -                   -   
64498                                     -                   -   
64499                                     -                   -   
64500                                     -                   -   

                                      Other_designatio

In [67]:
df_full_info = df.merge(df_gene_name, left_on=['GeneID'], right_on=['GeneID'])

In [69]:
df_full_info.to_csv('/grid/gillis/data/lohia/hi_c_data_processing/genomes_jlee/ensg_geneid_symbol.csv', sep='\t')

In [57]:
df['GeneID'].drop_duplicates()

0              1
1              2
2              3
3              9
4             10
          ...   
64496    8923215
64497    8923216
64498    8923217
64499    8923218
64500    8923219
Name: GeneID, Length: 64501, dtype: int64

In [15]:
df = pd.read_csv('/grid/gillis/data/lohia/eQTL/gtex_trans/GTEx_Analysis_v8_trans_eGenes_fdr05.txt', sep='\t' )


In [47]:


    exp_file_path=f'/grid/gillis/data/lohia/hi_c_data_processing/software/CoCoCoNet/networks/human_prioAggNet_minimal.h5'

    jac_sim = hm.hiCMatrix(exp_file_path)
    

    
   

In [ ]:
    SRP_name="aggregates"
    resolution="10kbp_raw"
    resol_human="10000"
    prediction_type="prediction"
    
    auc_KR = []
    auc_tss = []
    auc_gene_id = []
    auc_KR_ranked = []
    auc_KR_ranked_tss = []
    auc_jac_tss = []
    auc_jac = []
    auc_insulation_score = []
    auc_activity_score = []
    auc_var_insulation = []
    auc_var_insulation_median = []

    for var_int, gene_chr in zip(df_all_variants_subset['variant_id'].to_list(), df_all_variants_subset['gene_chr'].to_list()):
        #print (var_int)


        df_test = df_all_variants[df_all_variants['gene_chr'] != gene_chr]
        #df_test_negative = df_test[df_test['variant_id'] != var_int]
        #df_test_negative['prediction'] = 0
        #df_test_positive = df_test[df_test['variant_id'] == var_int]
        #df_test_positive['prediction'] = 1
        #df_test = pd.concat([df_test_negative, df_test_positive])
 
        #df_test = df_test[df_test['tss_distance'].abs() <= (int(distance_cutoff_in_bp)+200000+int(resol_human))]
        
        #df_test['nes'] = df_test['slope'].abs()
        #df_test['pval_st'] = 1/df_test['pval_nominal']
        df_test.drop_duplicates(['gene_bin'], keep='last', inplace=True)
        
        if df_test['prediction'].sum() != 0:
            if df_test.shape[0] > 1:
                bin_start = int(int(var_int.split('_')[1]) / int(resol_human))

                if bin_start in all_non_gene_index_list:

                            gene_bins = []
                            gene_name = []
                            non_gene_bins = []
                            variant_bins = [all_bins.index(bin_start)]


                            variant_name = [var_int]

                            for gene_x in df_test.drop_duplicates(subset = ['gene_id', 'variant_id'])['gene_id']:
                                    if gene_x in all_gene_list:
                                            gene_bins.append(all_gene_list.index(gene_x))
                                            gene_name.append(gene_x)

                                    else:
                                        continue


                            biny=gene_bins
                            binx=variant_bins
                            biny_name = gene_name
                            binx_name = variant_name




                            df_exp = pd.pivot_table(df_test, values=prediction_type, columns='gene_id',
                                                index='variant_id')


                            subset_genes_exp_file = list (set(df_exp.columns.to_list()) & set(biny_name))
                            df_exp_subset = df_exp.loc[:, subset_genes_exp_file]


                            if prediction_type == 'prediction':

                                exp_upper = lambda x: np.where(x <= 0 , 0, 1.0) if x[~np.isnan(x)].shape[0] > 0 else np.zeros(x.shape[0])
                                tp = np.apply_along_axis(exp_upper, 1, df_exp_subset)

                                exp_upper = lambda x: np.where(x > 0   , 0, 1.0) if x[~np.isnan(x)].shape[0] > 0 else np.zeros(x.shape[0])
                                tn = np.apply_along_axis(exp_upper, 1, df_exp_subset)
                            else:
                                exp_upper = lambda x: np.where(x < np.percentile(x[~np.isnan(x)] , 99), 0, 1.0) if x[~np.isnan(x)].shape[0] > 0 else np.zeros(x.shape[0])
                                tp = np.apply_along_axis(exp_upper, 1, df_exp_subset)
                                exp_upper = lambda x: np.where(x >= np.percentile(x[~np.isnan(x)] , 99), 0, 1.0) if x[~np.isnan(x)].shape[0] > 0 else np.zeros(x.shape[0])
                                tn = np.apply_along_axis(exp_upper, 1, df_exp_subset)



                            df_jac = pd.DataFrame(entire_matrix_KR[binx,:][:, biny].toarray() ,  index=binx_name, columns = biny_name)

                            df_jac_subset = df_jac.loc[:, subset_genes_exp_file]

                            rank_abs = lambda x: stats.rankdata(x)
                            predicts2 = np.apply_along_axis(rank_abs, 1, df_jac_subset)
                            predicts2 = predicts2.astype('float')

                            pos_rank_sum = tp * predicts2
                            auc_array = (((np.nansum(pos_rank_sum, axis=1) / (np.nansum(tp, axis=1)) )- (np.nansum(tp, axis=1) + 1)/2)) / np.nansum(tn, axis=1)
                            auc_KR.append(auc_array[0])

                            auc_insulation_score.append(auc_array[0])
                            auc_gene_id.append(var_int)
                            bin_start = int(int(var_int.split('_')[1]) / int(resol_human))
                            auc_var_insulation.append(df_all_variants_subset.shape[0])
                            #auc_var_insulation.append(insulation_scores_dict_orignal[bin_start])
                            auc_KR_ranked_tss.append(df_test.shape[0])
                            auc_jac_tss.append(df_test['prediction'].sum())
                            #auc_var_insulation_median.append(insulation_scores_dict[bin_start])
                            auc_var_insulation_median.append(df_all_variants_subset.shape[0])
                            auc_activity_score.append(df_all_variants_subset.shape[0])
                else:
                    continue
            else:
                continue
        else:
            continue
        df = pd.DataFrame(columns = ['auc_KR', 'gene', 'auc_insulation', 'auc_activity', 'auc_var_insulation', 'auc_var_insulation_median'])  
        df['auc_KR'] = auc_KR
        df['gene'] = auc_gene_id
        df['auc_insulation'] = auc_insulation_score
        df['auc_activity'] = auc_activity_score
        df['auc_var_insulation'] = auc_var_insulation
        df['auc_var_insulation_median'] = auc_var_insulation_median
        print (df['auc_KR'].median())
    df.to_csv(f'/grid/gillis/data/lohia/hi_c_data_processing/data_human/{SRP_name}/{resolution}/temp.csv', sep='\t', index=False)
    
    

In [38]:
    df_all_variants_subset = df_unique_variants_sig.drop_duplicates(['variant_id'])
    
    df_all_variants_subset['gene_id'] = [x.split('.')[0] for x in df_all_variants_subset['gene_id']]
    df_all_variants_subset['chr_var'] = [x.split('_')[0] for x in df_all_variants_subset['variant_id']]
    df_all_variants_subset['tss_var'] = [x.split('_')[1] for x in df_all_variants_subset['variant_id']]

<ipython-input-38-d89f3fb66b70>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_all_variants_subset['gene_id'] = [x.split('.')[0] for x in df_all_variants_subset['gene_id']]
<ipython-input-38-d89f3fb66b70>:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_all_variants_subset['chr_var'] = [x.split('_')[0] for x in df_all_variants_subset['variant_id']]
<ipython-input-38-d89f3fb66b70>:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer

In [40]:
df_all_variants_subset = df_all_variants_subset[df_all_variants_subset['gene_id'].isin(all_gene_list)]

In [41]:
df_all_variants_subset 

tissue_id          gene_id     gene_name  \
0            Brain_Cerebellar_Hemisphere  ENSG00000071994         PDCD2   
1                           Nerve_Tibial  ENSG00000157087        ATP2B2   
2                           Nerve_Tibial  ENSG00000116661         FBXO2   
3                           Nerve_Tibial  ENSG00000172508        CARNS1   
4                           Nerve_Tibial  ENSG00000176177        ENTHD1   
..                                   ...              ...           ...   
156  Esophagus_Gastroesophageal_Junction  ENSG00000230676   RP11-65J3.3   
158                 Minor_Salivary_Gland  ENSG00000260807  RP11-161M6.2   
159                 Minor_Salivary_Gland  ENSG00000261526   CTB-31O20.2   
160                              Thyroid  ENSG00000231231     LINC01423   
161                      Muscle_Skeletal  ENSG00000230676   RP11-65J3.3   

    gene_chr         biotype  gene_mappability  \
0       chr6  protein_coding           0.94033   
1       chr3  protein_coding           0.99981   
2       chr1  protein_coding           0.99716   
3      chr11  protein_coding           0.99796   
4      chr22  protein_coding           1.00000   
..       ...             ...               ...   
156     chr9         lincRNA           0.99118   
158    chr16         lincRNA           0.99323   
159    chr19         lincRNA           0.82163   
160    chr21         lincRNA           1.00000   
161     chr9         lincRNA           0.99118   

                                       variant_id  tissue_af    slope  \
0                             chr1_788439_T_A_b38    0.08000  0.97653   
1                          chr17_61209908_C_T_b38    0.68609  0.31593   
2                          chr17_61209283_G_C_b38    0.70207  0.30169   
3                          chr18_26533336_C_T_b38    0.45207  0.24687   
4                          chr19_57779860_A_G_b38    0.60150 -0.28482   
..                                            ...        ...      ...   
156                        chr22_23511498_C_T_b38    0.84545  0.59698   
158                        chr12_63508078_A_G_b38    0.27778  0.28142   
159                        chr3_20722938_G_GA_b38    0.36806  0.47175   
160                        chr16_85142272_A_G_b38    0.93902 -0.68896   
161  chr22_23514454_CTAGACAGCCCTCGGGAGGGAGT_C_b38    0.19476  0.54580   

     slope_se  pval_nominal           fdr  prediction chr_var   tss_var  
0    0.104930  3.201900e-16  4.746180e-06           1    chr1    788439  
1    0.033239  1.096000e-19  1.643560e-09           1   chr17  61209908  
2    0.033103  2.437500e-18  1.827640e-08           1   chr17  61209283  
3    0.028420  6.507100e-17  3.252680e-07           1   chr18  26533336  
4    0.035560  9.456900e-15  3.545390e-05           1   chr19  57779860  
..        ...           ...           ...         ...     ...       ...  
156  0.073405  1.451300e-14  2.481720e-05           1   chr22  23511498  
158  0.038394  3.029300e-11  3.518100e-02           1   chr12  63508078  
159  0.064716  3.726800e-11  3.518100e-02           1    chr3  20722938  
160  0.098736  9.478900e-12  1.895780e-02           1   chr16  85142272  
161  0.046776  1.214900e-28  1.518620e-19           1   chr22  23514454  

[142 rows x 15 columns]